
# Arc Coverage Model

This example demonstrates the ArcCoverageModel which ensures complete gas treatment
by the arc through coverage fraction calculation.


In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import openmdao.api as om

from paroto.models.coverage import ArcCoverageModel

# Create OpenMDAO problem
prob = om.Problem()
prob.model.add_subsystem("coverage", ArcCoverageModel())
prob.setup()

# Set parameters for typical operating conditions
prob.set_val("coverage.gap_distance", 0.01)  # 10 mm
prob.set_val("coverage.torch_diameter", 0.02)  # 20 mm
prob.set_val("coverage.pulse_frequency", 50e3)  # 50 kHz
prob.set_val("coverage.flow_velocity", 1.0)  # 1 m/s
prob.set_val("coverage.thermal_diameter", 0.003)  # 3 mm arc

# Run model
prob.run_model()

# Extract results
coverage = prob.get_val("coverage.coverage_fraction")[0]
margin = prob.get_val("coverage.coverage_margin")[0]
satisfied = prob.get_val("coverage.coverage_constraint_satisfied")[0]

print("=" * 50)
print("Arc Coverage Model - Gas Coverage")
print("=" * 50)
print(f"Coverage Fraction: {coverage:.2f}")
print(f"Margin: {margin:.3e} m³/s")
print(f"Constraint Satisfied: {'Yes' if satisfied > 0.5 else 'No'}")
print("=" * 50)

if coverage >= 1.0:
    print("[OK] All gas is treated by the arc")
else:
    print(f"[FAIL] Only {coverage * 100:.1f}% of gas is treated")
    print("  Increase frequency or arc diameter, or reduce velocity")

# Plot coverage vs pulse frequency
print("\nGenerating plot: Coverage vs Pulse Frequency...")
freq_range = np.logspace(3, 6, 50)  # 1 kHz to 1 MHz
coverage_values = []

for freq in freq_range:
    prob.set_val("coverage.pulse_frequency", freq)
    prob.run_model()
    coverage_values.append(prob.get_val("coverage.coverage_fraction")[0])

plt.figure(figsize=(8, 5))
plt.semilogx(freq_range / 1e3, coverage_values, "b-", linewidth=2)
plt.axhline(y=1.0, color="r", linestyle="--", label="Complete Coverage")
plt.axvline(x=50, color="g", linestyle=":", alpha=0.7, label="Nominal (50 kHz)")
plt.xlabel("Pulse Frequency (kHz)")
plt.ylabel("Coverage Fraction")
plt.title("Arc Coverage vs Pulse Frequency")
plt.grid(True, alpha=0.3)
plt.legend()
plt.ylim([0, max(coverage_values) * 1.1])
plt.tight_layout()
plt.show()